# Ordinary Differential Equations

In [1]:
using DifferentialEquations
using WGLMakie

In [ ]:
] add DifferentialEquations

    Updating registry at `~/.julia/registries/General.toml`
   Resolving package versions...
   Installed Sundials_jll ───────────────────── v5.2.2+0
   Installed FunctionWrappers ───────────────── v1.1.3
   Installed TimerOutputs ───────────────────── v0.5.23
   Installed Polyester ──────────────────────── v0.7.9
   Installed MaybeInplace ───────────────────── v0.1.1
   Installed NonlinearSolve ─────────────────── v3.5.0
   Installed RecursiveArrayTools ────────────── v3.6.2
   Installed TriangularSolve ────────────────── v0.1.20
   Installed DifferentialEquations ──────────── v7.12.0
   Installed Static ─────────────────────────── v0.8.8
   Installed SLEEFPirates ───────────────────── v0.6.42
   Installed RandomNumbers ──────────────────── v1.5.3
   Installed SteadyStateDiffEq ──────────────── v2.0.1
   Installed BoundaryValueDiffEq ────────────── v5.6.0
   Installed Tricks ─────────────────────────── v0.1.8
   Installed SIMDTypes ──────────────────────── v0.1.0
   Installed ArnoldiM

In [5]:
function RK(x_0, y_0, f, h, N)
    for i in 1:N
        ys = [y_0]
        k_0 = f(x_0, y_0)
        y_1 = y_0 + h * k_0 / 2
        x_1 = x_0 + h / 2
        k_1 = f(x_1, y_1)
        y_2 = y_0 + h  * k_1
        x_0 += h
        push!(ys, y_2)
    end
    
end

RK (generic function with 1 method)

## Harmonic Oscillator

Conditions
$$ x, v $$

$$ \dot{x} = v $$
$$ \dot{v} = -x$$

In [6]:
function fho(U::Vector)
    x, v = U
    xdot = v
    vdot = -x
    [xdot, vdot]
end

fho (generic function with 1 method)

In [7]:
fho([1, 0])

2-element Vector{Int64}:
  0
 -1

In [2]:
function eulerStep(f, y0, h)
    k0 = f(y0)
    y1 = y0 + h * k0
    y1
end

eulerStep (generic function with 1 method)

In [3]:
function eulerMethod(f, U0, h, N)
    Us = []
    U = U0
    for i in 1:N
        U = eulerStep(f, U, h)
        push!(Us, U)
    end
    Us
end

eulerMethod (generic function with 1 method)

In [4]:
eulerMethod(fho, [1.,0.], 0.001, 1000)

LoadError: UndefVarError: `fho` not defined

# Earth orbit around the sun
State-vector: $[r, k, \theta]$
$$
\begin{cases}
    \dot{\theta} = l / r^2 \\
    \dot{r} = k \\
    \dot{k} = r \dot{\theta}^2 - \frac{GM}{r^2} 
\end{cases}
$$
Define $k = \dot{r}$

In [20]:
function orbitalMechanics(U::Vector)

    r, k, t = U
    tdot = 1 / r^2
    rdot = k
    kdot = r * tdot^2 - 1 / r^2
    [rdot, kdot, tdot]
end

orbitalMechanics (generic function with 1 method)

In [69]:
sol = eulerMethod(orbitalMechanics, [1, -0.1, 0], 0.1, 1000)

1000-element Vector{Any}:
 [0.99, -0.1, 0.1]
 [0.98, -0.09896938984787162, 0.2020304050607081]
 [0.9701030610152128, -0.09684442490979309, 0.30615368702655565]
 [0.9604186185242335, -0.09356971299244593, 0.41241232629989305]
 [0.9510616472249889, -0.0891017534073009, 0.5208247013205656]
 [0.9421514718842587, -0.08341291835458083, 0.6313807893218328]
 [0.9338101800488007, -0.07649572173572293, 0.744037881698163]
 [0.9261606078752284, -0.06836712857818163, 0.8587165897771922]
 [0.9193238950174102, -0.05907256084232794, 0.975297485914985]
 [0.9134166389331774, -0.04868916819418067, 1.0936187778867517]
 [0.9085477221137593, -0.037327877158107606, 1.2134754356122741]
 [0.9048149343979486, -0.025133733819717587, 1.3346201616846445]
 [0.9023015610159768, -0.012284136057707342, 1.4567665076742695]
 ⋮
 [32.3074356091676, 0.685571908693339, 42.13986344654115]
 [32.37599280003693, 0.6854790676454262, 42.139959253052254]
 [32.444540706801476, 0.6853866131160461, 42.1400546542463]
 [32.513079368113

In [70]:
data = reshape(vcat(sol...), (3, :));
rs = data[begin,:];
ts = data[end,:];

In [71]:
f = Figure()
Axis(f[1,1])
lines!(rs .* cos.(ts), rs .* sin.(ts))
f

State-vector: $[x, y, v_x, v_y]$

$F = m a \Rightarrow a= - \frac{G M}{r^2}\hat{r}$

$$
\begin{cases}
    \dot{x} = v_x \\
    \dot{y} = v_y \\
    \dot{v}_x = - \frac{G M}{m r^2} \frac{x}{r} \\
    \dot{v}_y = - \frac{G M}{m r^2}\frac{y}{r}
\end{cases}
$$
Define $k = \dot{r}$

In [36]:
function orbitalMechanicsCartesian(U::Vector)
    M = 2e30
    m = 5.972e22
    G = 6.67e-11 * (365 * 24 * 60 * 60)^2 / (1.496e+11)^2
    x, y, vx, vy = U
    r = sqrt(x^2 + y^2)
    xdot = vx
    ydot = vy
    vxdot = -4 * pi^2 * x / r^3
    vydot = -4 * pi^2 * y / r^3
    [xdot, ydot, vxdot, vydot]
end

orbitalMechanicsCartesian (generic function with 1 method)

In [44]:
sol = eulerMethod(orbitalMechanicsCartesian, [1, 0, 0, 2 * pi / 365], 0.0001, 100)
data = reshape(vcat(sol...), (4, :));
xs = data[1,:];
ys = data[2,:];

In [43]:
f = Figure()
Axis(f[1,1])
lines!(xs, ys)
f

π = 3.1415926535897...

In [ ]:
sol = eulerMethod(orbitalMechanicsCartesian, [1, 0, 0, 2 * pi / 365], 0.01, 10000)
data = reshape(vcat(sol...), (4, :));
xs = data[1,:];
ys = data[2,:];

In [24]:
6.67e-11 * (365 * 24 * 60 * 60)^2 / (1.496e+11)^2

2.963984039577912e-18